# TfL and Rest API's

## RestAPI's and Python Requests

Transport for London (TfL) offers an easily accessible open data service. This information is conveniently obtainable through a **RestAPI**. API is short for *Application Programming Interface*, which is the designated interface for programming with a software. This can occur through various means, such as Grasshopper communicating with Rhino via an API. A *RestAPI* is more specific, as it involves communicating with a webserver through HTTP requests.

Essentially, this implies that you must create a specific text sequence that you can copy into your web browser. The browser then transmits this sequence to a webserver, which responds with the requested information.

Python provides several methods to send requests to a webserver, with the most popular approach being the utilization of a library known as [**"Requests"**](https://requests.readthedocs.io/en/latest/#).


![](https://upload.wikimedia.org/wikipedia/commons/thumb/a/aa/Requests_Python_Logo.png/187px-Requests_Python_Logo.png)


## Transport for London - TfL

![](https://www.t-three.com/hubfs/tp-2017/clients/tfl/TFL-logo.png)


This is the link to the [open data landing page](https://tfl.gov.uk/info-for/open-data-users/). Take your time and read a few of the posts, there are some interesting entries.

And this is the link to the [API Portal that](https://api-portal.tfl.gov.uk/api-details) helps you with building up the query.

You have the option to utilize the service anonymously, without any need for a subscription. Under this circumstance, you can make 50 requests per minute. However, if you subscribe (at no cost), you can send up to 500 requests per minute.

### TfL Example Air Quality
The following code demonstrates the typical setup with Requests. It's important to note that there are two options: one involving both a password and an ID, and another that doesn't require any authentication. For the sake of simplicity, we are using the code that doesn't require authentication.

In [1]:
import requests

# Your ID and Key that you get from TfL
api_id = '...'
api_key = '...'

# Make a GET request to a specific endpoint
url = 'https://api.tfl.gov.uk/AirQuality/'

#OPTION 01 with password
#headers = {'App-ID': api_id, 'App-Key': api_key}
#response = requests.get(url, headers=headers)
#response = requests.get(url)

#OPTION 02 anoymous
response = requests.get(url)

# Check the status of the response
if response.status_code == 200:
    # Process the response data
    data = response.json()
    # Do something with the data
    
else:
    print(f'Request failed with status code {response.status_code}')

#### Parsing the results

We have now an object called `data` that holds the response from TfL. If you have a look a the code you will see this line:

`data = response.json()`

This implies that we need to instruct Python that the incoming response is in the form of a text file in JSON format. While there are various formats available, JSON is the most widely used. The basic structure is this:
```python
{ "name": "Zophie",
  "isCat": true,
  "miceCaught": 0,
  "napsTaken": 37.5,
  "felineIQ": null}

```
Notice the similarity to a python dict object:
```python
{ "brand": "Ford",
  "model": "Mustang",
  "year": 1964 }
```
As a reminder, a python list looks like this: 
```python
[
"Car 1", 
"Car 2", 
"Car 3"
]
```
As you might suspect, JSON Objects can be arraged in arrays: 
```python
[
{ "brand": "BMW",
  "model": "Z1",
  "year": 1995 } , 
{"brand": "Ford",
  "model": "Mustang",
  "year": 1964 }, 
{"brand": "VW",
  "model": "Polo",
  "year": 2020 }
]
```
it also goes the other way: 
```python
{ 
"brand" : ["BMW", "Ford", "VW"]
"model" : ["Z1", "Mustang", "Polo"]
"year"  : [1995, 1964, 2020]
}
```

With this in mind, let's have a look at the answer from TfL. 

Understanding nextled JSON data is not always straightforward. The **pprint module** can help you to print the data in a more readable format.

In [3]:
import pprint

pprint.pprint(data, compact=True)
# print(data)

{'$id': '1',
 '$type': 'Tfl.Api.Presentation.Entities.LondonAirForecast, '
          'Tfl.Api.Presentation.Entities',
 'currentForecast': [{'$id': '2',
                      '$type': 'Tfl.Api.Presentation.Entities.CurrentForecast, '
                               'Tfl.Api.Presentation.Entities',
                      'forecastBand': 'Low',
                      'forecastID': '47639',
                      'forecastSummary': 'Low air pollution forecast valid '
                                         'from Friday 10 January to end of '
                                         'Saturday 11 January GMT',
                      'forecastText': 'Staying cold, with widespread and '
                                      'locally severe frosts overnight and '
                                      'some cloud cover on Friday morning. '
                                      'Cold with wintry sunshine on '
                                      'Saturday.&lt;br/&gt;&lt;br/&gt;A '
                  

In [10]:
# pprint.pprint(data['$id'])
pprint.pprint(data['currentForecast'], compact=True)
# print(data['currentForecast'][0]["forecastSummary"])

[{'$id': '2',
  '$type': 'Tfl.Api.Presentation.Entities.CurrentForecast, '
           'Tfl.Api.Presentation.Entities',
  'forecastBand': 'Low',
  'forecastID': '47639',
  'forecastSummary': 'Low air pollution forecast valid from Friday 10 January '
                     'to end of Saturday 11 January GMT',
  'forecastText': 'Staying cold, with widespread and locally severe frosts '
                  'overnight and some cloud cover on Friday morning. Cold with '
                  'wintry sunshine on Saturday.&lt;br/&gt;&lt;br/&gt;A '
                  'relatively &#39;clean&#39; north easterly air flow, from '
                  'the North Sea via the UK. This breeze throughout the day '
                  'should ensure good dispersion of any local pollution '
                  'emissions.&lt;br/&gt;&lt;br/&gt;Air pollution is expected '
                  'to remain &#39;Low&#39; for the following '
                  'pollutants:&lt;br/&gt;&lt;br/&gt;Nitrogen '
                  'Dioxide&

 Alternativlly, you can use online resources like [jsonformatter](https://jsonformatter.curiousconcept.com/#)

In [11]:
for entry in data['currentForecast']:
  print (entry['forecastType'])
  print (entry['forecastSummary'])
  

Current
Low air pollution forecast valid from Friday 10 January to end of Saturday 11 January GMT
Future
Low air pollution forecast valid from Friday 10 January to end of Saturday 11 January GMT


### TfL Bikepoints London - Parsing and Export as csv

This excercise will examine the entirety of the bicycle locations in London. Given that the file is already substantial, it presents an excellent opportunity to analyze the response, construct a data frame, and store the data as a CSV. This process represents a common and standard workflow.

In [12]:
import requests
import pandas as pd

url = 'https://api.tfl.gov.uk/BikePoint/'
response = requests.get(url)

bikepoints = response.json()

In [13]:
pprint.pprint(bikepoints, compact=True)

[{'$type': 'Tfl.Api.Presentation.Entities.Place, Tfl.Api.Presentation.Entities',
  'additionalProperties': [{'$type': 'Tfl.Api.Presentation.Entities.AdditionalProperties, '
                                     'Tfl.Api.Presentation.Entities',
                            'category': 'Description',
                            'key': 'TerminalName',
                            'modified': '2025-01-10T12:16:41.17Z',
                            'sourceSystemKey': 'BikePoints',
                            'value': '001023'},
                           {'$type': 'Tfl.Api.Presentation.Entities.AdditionalProperties, '
                                     'Tfl.Api.Presentation.Entities',
                            'category': 'Description',
                            'key': 'Installed',
                            'modified': '2025-01-10T12:16:41.17Z',
                            'sourceSystemKey': 'BikePoints',
                            'value': 'true'},
                           {'$type':

In [34]:
pprint.pprint(bikepoints[4])

{'$type': 'Tfl.Api.Presentation.Entities.Place, Tfl.Api.Presentation.Entities',
 'additionalProperties': [{'$type': 'Tfl.Api.Presentation.Entities.AdditionalProperties, '
                                    'Tfl.Api.Presentation.Entities',
                           'category': 'Description',
                           'key': 'TerminalName',
                           'modified': '2025-01-04T22:16:39.423Z',
                           'sourceSystemKey': 'BikePoints',
                           'value': '003420'},
                          {'$type': 'Tfl.Api.Presentation.Entities.AdditionalProperties, '
                                    'Tfl.Api.Presentation.Entities',
                           'category': 'Description',
                           'key': 'Installed',
                           'modified': '2025-01-04T22:16:39.423Z',
                           'sourceSystemKey': 'BikePoints',
                           'value': 'true'},
                          {'$type': 'Tfl.Api.Pres

In [17]:
bikepoints[5]

id = bikepoints[5]['id']
commonName = bikepoints[0]['commonName']
lat = bikepoints[5]['lat']
lon = bikepoints[5]['lon']

print( "ID: " + str(id) + " / Name: " + str(commonName) + " / Latitude: " + str(lat) + " / Longitude: " + str(lon))

ID: BikePoints_6 / Name: River Street , Clerkenwell / Latitude: 51.518117 / Longitude: -0.144228


For all values it would be:

In [18]:
for entry in bikepoints:
  id = entry['id']
  commonName = entry['commonName']
  lat = entry['lat']
  lon = entry['lon']
  print( "ID: " + str(id) + " / Name: " + str(commonName) + " / Latitude: " + str(lat) + " / Longitude: " + str(lon))

ID: BikePoints_1 / Name: River Street , Clerkenwell / Latitude: 51.529163 / Longitude: -0.10997
ID: BikePoints_2 / Name: Phillimore Gardens, Kensington / Latitude: 51.499606 / Longitude: -0.197574
ID: BikePoints_3 / Name: Christopher Street, Liverpool Street / Latitude: 51.521283 / Longitude: -0.084605
ID: BikePoints_4 / Name: St. Chad's Street, King's Cross / Latitude: 51.530059 / Longitude: -0.120973
ID: BikePoints_5 / Name: Sedding Street, Sloane Square / Latitude: 51.49313 / Longitude: -0.156876
ID: BikePoints_6 / Name: Broadcasting House, Marylebone / Latitude: 51.518117 / Longitude: -0.144228
ID: BikePoints_7 / Name: Charlbert Street, St. John's Wood / Latitude: 51.5343 / Longitude: -0.168074
ID: BikePoints_8 / Name: Maida Vale, Maida Vale / Latitude: 51.529857 / Longitude: -0.183486
ID: BikePoints_9 / Name: New Globe Walk, Bankside / Latitude: 51.507385 / Longitude: -0.09644
ID: BikePoints_10 / Name: Park Street, Bankside / Latitude: 51.505974 / Longitude: -0.092754
ID: BikePoin

Great, but now we like to have it as a panda dataframe:

In [19]:
df = pd.DataFrame(bikepoints, columns=['id','commonName','lat','lon'])

df

id                            commonName        lat       lon
0      BikePoints_1            River Street , Clerkenwell  51.529163 -0.109970
1      BikePoints_2        Phillimore Gardens, Kensington  51.499606 -0.197574
2      BikePoints_3  Christopher Street, Liverpool Street  51.521283 -0.084605
3      BikePoints_4       St. Chad's Street, King's Cross  51.530059 -0.120973
4      BikePoints_5         Sedding Street, Sloane Square  51.493130 -0.156876
..              ...                                   ...        ...       ...
791  BikePoints_272                 Baylis Road, Waterloo  51.501444 -0.110699
792  BikePoints_354         Northumberland Avenue, Strand  51.506767 -0.123702
793  BikePoints_309            Embankment (Savoy), Strand  51.509631 -0.119047
794  BikePoints_857                        Strand, Strand  51.512582 -0.115057
795  BikePoints_564                Somerset House, Strand  51.509943 -0.117619

[796 rows x 4 columns]

That was fast, it works so well because we do not access nesteld values and the column names remain as per the json file. All we have to do is to save the file as csv.

In [20]:
filepath = "BikePointsLocation.csv"

df.to_csv(path_or_buf = filepath, header = ("ID", "commonName", "lat", "lon"))

And the comlpete script looks like this (less than ten lines of code):

In [16]:
import requests
import pandas as pd

url = 'https://api.tfl.gov.uk/BikePoint/'
response = requests.get(url)

data = response.json()

df = pd.DataFrame(data, columns=['id','commonName','lat','lon'])

filepath = "/content/drive/MyDrive/Colab Notebooks/RC15 23 Excercises/Excercise 06 - Download Data from TfL/BikePointsLocation.csv"

df.to_csv(path_or_buf = filepath, header = ("ID", "commonName", "lat", "lon"))

### Display in Folium

In [21]:
import folium
import requests
import pandas as pd

center = [51.5147785742626, -0.11480186769662788]
map_london = folium.Map(location=center, tiles = "Cartodb dark_matter", zoom_start=12)

url = 'https://api.tfl.gov.uk/BikePoint/'
response = requests.get(url)

data = response.json()

df = pd.DataFrame(data, columns=['id','commonName','lat','lon'])

latitudes = df['lat']
longitudes = df['lon']

for latitude, longitude in  zip(latitudes,longitudes):
  coordinate = [latitude,longitude]
  radius = 1
  folium.CircleMarker(
    location=coordinate,
    radius=radius,
    color="cornflowerblue",
    stroke=False,
    fill=True,
    fill_opacity=0.6,
    opacity=1,
    ).add_to(map_london)


map_london

---
## Traffic Webcams (Jam Cams) from TfL  

*As of early January 2025, [Jam Cams](https://www.tfljamcams.net/) are currently offline due to a security breach. As a result, the code below is unlikely to function.*  

The *Places API* is quite useful, as it provides information about all TfL features within a specified radius of a given point. You can find the documentation [here](https://api-portal.tfl.gov.uk/api-details#api=Place&operation=Place_MetaPlaceTypes).  

Here are the available placetypes:  


In [22]:
import requests
url = "https://api.tfl.gov.uk/Place/Meta/PlaceTypes"

response = requests.get(url)

data = response.json()

import pprint

pprint.pprint(data)


['AreaForIntensification',
 'BikePoint',
 'Boroughs',
 'Cabwise',
 'CarPark',
 'CensusOutputAreas',
 'CensusSuperOutputAreas',
 'CentralActivityZone',
 'ChargeConnector',
 'ChargeStation',
 'CoachBay',
 'CoachPark',
 'CyclePark',
 'JamCam',
 'OnStreetMeteredBay',
 'OpportunityAreas',
 'OtherCoachParking',
 'OysterTicketShop',
 'RedLightAndSpeedCam',
 'RedLightCam',
 'SpeedCam',
 'TaxiRank',
 'VariableMessageSign',
 'Wards',
 'WaterfreightBridge',
 'WaterfreightDock',
 'WaterfreightJetty',
 'WaterfreightLock',
 'WaterfreightOther Access Point',
 'WaterfreightTunnel',
 'WaterfreightWharf']


And with the help of the documentation, we can easy get the query code:

In [ ]:
url = "https://api.tfl.gov.uk/Place/?Lat=51.504593&Lon=-0.076641&radius=3000&type=JamCam"

response = requests.get(url)

data = response.json()

import pprint

pprint.pprint(data, compact=True)


{'$type': 'Tfl.Api.Presentation.Entities.PlacesResponse, '
          'Tfl.Api.Presentation.Entities',
 'centrePoint': [51.504, -0.076],
 'places': [{'$type': 'Tfl.Api.Presentation.Entities.Place, '
                      'Tfl.Api.Presentation.Entities',
             'additionalProperties': [{'$type': 'Tfl.Api.Presentation.Entities.AdditionalProperties, '
                                                'Tfl.Api.Presentation.Entities',
                                       'category': 'Description',
                                       'key': 'TerminalName',
                                       'modified': '2025-01-10T12:18:50.5Z',
                                       'sourceSystemKey': 'BikePoints',
                                       'value': '001213'},
                                      {'$type': 'Tfl.Api.Presentation.Entities.AdditionalProperties, '
                                                'Tfl.Api.Presentation.Entities',
                                       'cat

We take the first object and we extract the info we want:

In [3]:
print ( "There are " + str(len(data["places"])) + " JamCam.")

entry = data["places"][2]

id = entry["id"]
commonName = entry["commonName"]
lat = entry["lat"]
lon = entry["lon"]
imageURL = entry["additionalProperties"][1]["value"]

print("ID"               + "\t\t"   + str(id) + "\n" \
      + "commonName"     + "\t"   + str(commonName) + "\n" \
      + "lat"            + "\t\t"   + str(lat) + "\n" \
      + "lon"            + "\t\t"   + str(lon) + "\n" \
      + "imageURL"       + "\t"   + str(imageURL))

There are 0 JamCam.


IndexError: list index out of range

and now all of them into a csv list

In [48]:
import pandas as pd

df = pd.DataFrame(columns=['ID', 'commonName', 'lat', 'lon', 'imageURL'])

for entry in data["places"]:
  id = entry["id"]
  commonName = entry["commonName"]
  lat = entry["lat"]
  lon = entry["lon"]
  imageURL = entry["additionalProperties"][1]["value"]
  df.loc[len(df)] = [id,commonName,lat,lon,imageURL]

df

ID             commonName      lat      lon  \
0  JamCams_00001.03506      Tooley St/Boss St  51.5020 -0.07681   
1  JamCams_00001.03505  Tooley St/Abbots Lane  51.5039 -0.08136   
2  JamCams_00001.03540   Tooley St/Jamaica Rd  51.5005 -0.07445   

                                            imageURL  
0  https://s3-eu-west-1.amazonaws.com/jamcams.tfl...  
1  https://s3-eu-west-1.amazonaws.com/jamcams.tfl...  
2  https://s3-eu-west-1.amazonaws.com/jamcams.tfl...